In [1]:
import numpy as np;
import pandas as pd;
import plotly.express as px;


## Initialize Parameters

In [2]:
# Global parameters
NO_OF_DAYS = 400
modelParameter = {}
modelParameter["pi"] = 0.02
modelParameter["tE"] = 5
modelParameter["tI"] = 5
modelParameter["tH"] = 9
modelParameter["mu"] = 0.01
modelParameter["cw"] = 15
modelParameter["ch"] = 5

district = "tvm"

print(modelParameter)


{'pi': 0.02, 'tE': 5, 'tI': 5, 'tH': 9, 'mu': 0.01, 'cw': 15, 'ch': 5}


## Load and Initialize Data

In [3]:
## Population data
initDataDF = pd.read_csv("../data/" + district + "_init_data.csv")

cSparseMatrix = pd.read_csv("../output/" + district + "_cmatrix_results.csv")

## Number of regions
r = len(initDataDF.index)

## cijMatrix
cijMatrix = cSparseMatrix['Cij'].to_numpy().reshape(r,r)

## Sort distance data by name for easy matrix transformation
initDataDF.sort_values(by=['name'], inplace=True)
initDataDF

## Create cMatrix
cwMatrix = np.full((r,r),modelParameter["cw"], dtype=float)
np.fill_diagonal(cwMatrix, modelParameter["cw"] + modelParameter["ch"])
cwMatrix


array([[20., 15., 15., ..., 15., 15., 15.],
       [15., 20., 15., ..., 15., 15., 15.],
       [15., 15., 20., ..., 15., 15., 15.],
       ...,
       [15., 15., 15., ..., 20., 15., 15.],
       [15., 15., 15., ..., 15., 20., 15.],
       [15., 15., 15., ..., 15., 15., 20.]])

## Function definitions

In [4]:
## Differential equation
def deriv(y,contactRatio, modelParameter):
    Si, Ei, Ii, Hi, Ri = y
    dSdt = -modelParameter["pi"] * Si * contactRatio
    dEdt = (modelParameter["pi"] * Si * contactRatio) - (Ei/modelParameter["tE"])
    dIdt = (Ei/modelParameter["tE"]) -  (Ii/modelParameter["tI"])
    dHdt = (Ii/modelParameter["tI"]) - (Hi/modelParameter["tH"])
    dRdt = (Hi/modelParameter["tH"])
    return dSdt, dEdt, dIdt, dHdt, dRdt

In [5]:
## Find the contact ratio
def findSpatialContactRatioV2(Ci, I, N, cwi):
    c = cwi*Ci*I/N
    return c.sum()

In [6]:
## Find the contact ratio
def findSpatialContactRatio(name, NDict, yDict, cSparseMatrix, modelParameter):
    # TODO conver this to a matrix operation
    contactRatio = 0;
    Ci = cSparseMatrix[cSparseMatrix['iName']==name]
    cw = modelParameter["cw"]
    ch = modelParameter["ch"]
    
    for index, Cij in Ci.iterrows():
        jName = Cij['jName']
        cij = cw*Cij['Cij']

        if(jName == name):
            cij = (cw+ch)*Cij['Cij']
            
        Ij = yDict[jName][2]
        Nj = NDict[jName]
        contactRatio = contactRatio +  (cij*Ij/Nj)
    return contactRatio;
        

In [7]:
## derive next count for SEIHR compartments
def derivNext(y, rates) :
    S,E,I,H, R = y
    dSdt, dEdt, dIdt, dHdt, dRdt = rates
    S1 = S + dSdt
    E1 = E + dEdt
    I1 = I + dIdt
    H1 = H + dHdt
    R1 = R + dRdt
    if S1 <= 0:
        S1 = 0
    if E1 <= 0:
        E1 = 0
    if I1 <=0:
        I1 = 0
    if H1 <= 0:
        H1 = 0
    if R1 <= 0:
        R1 = 0
        
    return S1, E1, I1, H1, R1


## Run the model for all regions

In [8]:
yPrevDict = {};
yNextDict = {};
data = []
IPrevArr = []
NArray = []


for index, row in initDataDF.iterrows():
    yPrevDict[row['name']] = row['S'], row['E'], row['I'], row['H'], row['R'] 
    IPrevArr.append(row['I'])
    NArray.append(row['S'] + row['E'] + row['I'] + row['H'] + row['R'])

IPrev = np.array(IPrevArr);
N = np.array(NArray);


for day in range(1,NO_OF_DAYS):
    INextArr = [];
    for index, row in initDataDF.iterrows():
        name = row['name'];
        y = yPrevDict[name]; 
        
        contactRatio = findSpatialContactRatioV2(cijMatrix[index], IPrev, N, cwMatrix[index]);
        rates = deriv(y, contactRatio, modelParameter)
        yNext = derivNext(y, rates) 
        
        yNextDict[name] = yNext
        data.append({'name': name, 'day': day, 'S': yNext[0], 'E': yNext[1], 'I': yNext[2], 'H': yNext[3], 'R': yNext[4]})
        INextArr.append(yNext[2])
    
    yPrevDict = yNextDict
    IPrev = np.array(INextArr);

resultsDF = pd.DataFrame(data);



In [9]:
resultsDF.head(10)

name  day             S         E    I    H    R
0      Amboori__Thiruvananthapuram    1  15919.999242  0.000758  0.0  0.0  0.0
1         Anad__Thiruvananthapuram    1  31686.996192  0.003808  0.0  0.0  0.0
2  Anchuthengu__Thiruvananthapuram    1  17395.999240  0.000760  0.0  0.0  0.0
3  Andoorkonam__Thiruvananthapuram    1  30780.994908  0.005092  0.0  0.0  0.0
4   Aruvikkara__Thiruvananthapuram    1  33395.992612  0.007388  0.0  0.0  0.0
5      Aryanad__Thiruvananthapuram    1  26360.998228  0.001772  0.0  0.0  0.0
6    Aryancodu__Thiruvananthapuram    1  24327.997850  0.002150  0.0  0.0  0.0
7  Athiyannoor__Thiruvananthapuram    1  26972.997871  0.002129  0.0  0.0  0.0
8  Attingal(M)__Thiruvananthapuram    1  37435.997184  0.002816  0.0  0.0  0.0
9       Azhoor__Thiruvananthapuram    1  27389.997468  0.002532  0.0  0.0  0.0

## Save Output

In [10]:
resultsDF.to_csv("../output/" + district + "_results.csv")

## Plot Results

In [11]:
fig = px.scatter(resultsDF, x="day", y="H", color="name")
fig.show()

In [12]:
import plotly.graph_objects as go
figGo = go.Figure()

for index, row in initDataDF.iterrows(): 
    figGo.add_trace(go.Scatter(
    x=resultsDF[resultsDF['name']==row['name']]['day'],
    y=resultsDF[resultsDF['name']==row['name']]['H'],
    name=row['name']))


figGo.update_layout(yaxis_type="log")
figGo.show()

In [13]:
idx = resultsDF.groupby(['name'])['H'].transform(max) == resultsDF['H']
resultsDF[idx].to_csv("../output/" + district + "_peak_results.csv")
resultsDF[idx]

name  day              S  \
12383  Thiruvananthapuram(C)__Thiruvananthapuram  161  363504.881223   
12574              Karakulam__Thiruvananthapuram  164   20082.736586   
12702               Vilappil__Thiruvananthapuram  165   14120.734017   
12703            Vilavoorkal__Thiruvananthapuram  165   12221.492650   
12709             Aruvikkara__Thiruvananthapuram  166   12725.866407   
...                                          ...  ...            ...   
13754                 Ottoor__Thiruvananthapuram  179    6183.399639   
13772                 Vakkam__Thiruvananthapuram  179    6358.745663   
13774             Varkala(M)__Thiruvananthapuram  179   15514.005378   
13779                Vettoor__Thiruvananthapuram  179    7179.967731   
13826           Navayikkulam__Thiruvananthapuram  180   14973.219303   

                  E             I              H              R  
12383  55836.406128  62593.063058  114872.014631  370059.634960  
12574   3056.375468   3437.496981    6298.604603   19541.786362  
12702   2190.240816   2439.392201    4391.058306   13070.574660  
12703   1861.967866   2091.373744    3821.742191   11764.423549  
12709   1963.513143   2212.493369    4054.237337   12439.889744  
...             ...           ...            ...            ...  
13754    960.606629   1081.934019    1972.968482    5886.091231  
13772    976.385798   1102.032366    2018.076640    6077.759533  
13774   2352.539509   2649.053123    4845.067543   14687.334448  
13779   1118.791871   1259.489578    2295.539815    6850.211004  
13826   2467.050496   2807.567641    5163.084579   15291.077982  

[77 rows x 7 columns]